In [1]:
# Notebook parameters. Values here are for development only and
# will be overridden when running via snakemake and papermill.

config_file = "../../../config/agam.yaml"
contig = "2RL"

In [2]:
# Parameters
contig = "X"
config_file = "/home/runner/work/selection-atlas/selection-atlas/config/afun.yaml"


In [3]:
from IPython.display import Markdown
from bokeh.io import output_notebook
from selection_atlas.setup import AtlasSetup
from selection_atlas.page_utils import AtlasPageUtils

# Initialise the atlas setup.
setup = AtlasSetup(config_file)
page_utils = AtlasPageUtils(setup=setup)

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Chromosome X

The plot below shows {term}`selection signal`s discovered in any of the mosquito {term}`cohort`s analysed. Hover over a signal for more information about the {term}`cohort` in which the signal was found, including the mosquito species, collection location and date range. Click on a signal to see the underlying selection scan data.

In [5]:
df_signals = page_utils.load_signals(contig=contig)

page_utils.plot_signals(df=df_signals, contig=contig)

In [6]:
def style_signals_table(
    df_signals,
):
    df_signals = df_signals[
        [
            "contig",
            "focus_pstart",
            "focus_pstop",
            "cohort_id",
            "cohort_label",
            "statistic",
            "delta_i",
        ]
    ]

    # Add focal_region column.
    df_signals = df_signals.assign(
        focal_region=df_signals["contig"]
        + " ( "
        + df_signals["focus_pstart"].apply(
            lambda x: "{:,}".format(
                x,
            )
        )
        + " - "
        + df_signals["focus_pstop"].apply(
            lambda x: "{:,}".format(
                x,
            )
        )
        + " )"
    )

    # Add url column.
    df_signals["url"] = "../cohort/" + df_signals["cohort_id"] + ".html"

    def make_clickable(x):
        url = x["url"]
        name = x["cohort_label"]
        return '<a href="{}" rel="noopener noreferrer" target="_blank">{}</a>'.format(
            url, name
        )

    # Add hyperlinked cohort_label column
    df_signals["cohort_label"] = df_signals.apply(make_clickable, axis=1)

    # Style the table.
    styled = (
        df_signals[["focal_region", "cohort_label", "statistic", "delta_i"]]
        .rename(
            columns={
                "focal_region": "Focal Region",
                "cohort_label": "Cohort Label",
                "statistic": "Statistic",
                "delta_i": "Delta i",
            }
        )
        .style.hide(axis="index")
    )

    return styled


style_signals_table(df_signals)